In [1]:
import pandas as pd
import numpy as np

# featuretools for automated feature engineering
import featuretools as ft

# matplotlit and seaborn for visualizations
import matplotlib.pyplot as plt
plt.rcParams['font.size'] = 22
import seaborn as sns

In [2]:
app_train = pd.read_csv("./home-credit-default-risk/application_train.csv").sort_values("SK_ID_CURR").reset_index(drop = True).loc[:1000, :]
app_test = pd.read_csv("./home-credit-default-risk/application_test.csv").sort_values("SK_ID_CURR").reset_index(drop = True).loc[:1000, :]
bureau = pd.read_csv("./home-credit-default-risk/bureau.csv").sort_values(["SK_ID_CURR", "SK_ID_BUREAU"]).reset_index(drop = True).loc[:1000, :]
bureau_balance = pd.read_csv("./home-credit-default-risk/bureau_balance.csv").sort_values("SK_ID_BUREAU").reset_index(drop = True).loc[:1000, :]
cash = pd.read_csv("./home-credit-default-risk/POS_CASH_balance.csv").sort_values(["SK_ID_CURR", "SK_ID_PREV"]).reset_index(drop = True).loc[:1000, :]
credit = pd.read_csv("./home-credit-default-risk/credit_card_balance.csv").sort_values(["SK_ID_CURR", "SK_ID_PREV"]).reset_index(drop = True).loc[:1000, :]
previous = pd.read_csv("./home-credit-default-risk/previous_application.csv").sort_values(["SK_ID_CURR", "SK_ID_PREV"]).reset_index(drop = True).loc[:1000, :]
installments = pd.read_csv("./home-credit-default-risk/installments_payments.csv").sort_values(["SK_ID_CURR", "SK_ID_PREV"]).reset_index(drop = True).loc[:1000, :]

In [3]:
app_train['set'] = 'train'
app_test['set'] = 'test'
app_test["TARGET"] = np.nan

app = pd.concat([app_train, app_test], ignore_index=True)

In [4]:
es = ft.EntitySet(id = 'clients')


In [5]:
es = es.add_dataframe(dataframe_name='app', dataframe=app, index='SK_ID_CURR')

es = es.add_dataframe(dataframe_name='bureau', dataframe=bureau, index='SK_ID_BUREAU')

es = es.add_dataframe(dataframe_name='previous', dataframe=previous, index='SK_ID_PREV')

# For entities that do not have a unique index, you need to create one
es = es.add_dataframe(dataframe_name='bureau_balance', dataframe=bureau_balance, 
                      make_index=True, index='bureaubalance_index')

es = es.add_dataframe(dataframe_name='cash', dataframe=cash, 
                      make_index=True, index='cash_index')

es = es.add_dataframe(dataframe_name='installments', dataframe=installments,
                      make_index=True, index='installments_index')

es = es.add_dataframe(dataframe_name='credit', dataframe=credit,
                      make_index=True, index='credit_index')

/Users/user/mambaforge/lib/python3.10/site-packages/woodwork/type_sys/inference_functions.py:27: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pdtypes.is_categorical_dtype(series.dtype):
/Users/user/mambaforge/lib/python3.10/site-packages/woodwork/type_sys/inference_functions.py:189: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  pdtypes.is_categorical_dtype(series.dtype)
/Users/user/mambaforge/lib/python3.10/site-packages/woodwork/type_sys/inference_functions.py:27: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pdtypes.is_categorical_dtype(series.dtype):
/Users/user/mambaforge/lib/python3.10/site-packages/woodwork/type_sys/utils.py:40: UserWarning: The argument 'infer_datetime_format' is deprecated a

In [6]:
# Add the relationships to the EntitySet
es = es.add_relationship(parent_dataframe_name='app', 
                               parent_column_name='SK_ID_CURR', 
                               child_dataframe_name='bureau', 
                               child_column_name='SK_ID_CURR')
es = es.add_relationship(parent_dataframe_name='bureau', 
                                   parent_column_name='SK_ID_BUREAU', 
                                   child_dataframe_name='bureau_balance', 
                                   child_column_name='SK_ID_BUREAU')
es = es.add_relationship(parent_dataframe_name='app', 
                                 parent_column_name='SK_ID_CURR', 
                                 child_dataframe_name='previous', 
                                 child_column_name='SK_ID_CURR')
es = es.add_relationship(parent_dataframe_name='previous', 
                                  parent_column_name='SK_ID_PREV', 
                                  child_dataframe_name='cash', 
                                  child_column_name='SK_ID_PREV')
es = es.add_relationship(parent_dataframe_name='previous', 
                                          parent_column_name='SK_ID_PREV', 
                                          child_dataframe_name='installments', 
                                          child_column_name='SK_ID_PREV')
es = es.add_relationship(parent_dataframe_name='previous', 
                                    parent_column_name='SK_ID_PREV', 
                                    child_dataframe_name='credit', 
                                    child_column_name='SK_ID_PREV')

In [7]:
print(es)

Entityset: clients
  DataFrames:
    app [Rows: 2002, Columns: 123]
    bureau [Rows: 1001, Columns: 17]
    previous [Rows: 1001, Columns: 37]
    bureau_balance [Rows: 1001, Columns: 4]
    cash [Rows: 1001, Columns: 9]
    installments [Rows: 1001, Columns: 9]
    credit [Rows: 1001, Columns: 24]
  Relationships:
    bureau.SK_ID_CURR -> app.SK_ID_CURR
    bureau_balance.SK_ID_BUREAU -> bureau.SK_ID_BUREAU
    previous.SK_ID_CURR -> app.SK_ID_CURR
    cash.SK_ID_PREV -> previous.SK_ID_PREV
    installments.SK_ID_PREV -> previous.SK_ID_PREV
    credit.SK_ID_PREV -> previous.SK_ID_PREV


In [8]:
# Default primitives from featuretools
default_agg_primitives =  ["sum", "std", "max", "skew", "min", "mean", "count", "percent_true", "num_unique", "mode"]
default_trans_primitives =  ["day", "year", "month", "weekday", "haversine", "num_words", "num_characters"]

# DFS with specified primitives
feature_names = ft.dfs(entityset=es, target_dataframe_name='app',
                       trans_primitives=default_trans_primitives,
                       agg_primitives=default_agg_primitives, 
                       max_depth=2, features_only=True)

print('%d Total Features' % len(feature_names))

2209 Total Features


/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/synthesis/dfs.py:321: UnusedPrimitiveWarning: Some specified primitives were not used during DFS:
  trans_primitives: ['day', 'haversine', 'month', 'num_characters', 'num_words', 'weekday', 'year']
This may be caused by a using a value of max_depth that is too small, not setting interesting values, or it may indicate no compatible columns for the primitive were found in the data. If the DFS call contained multiple instances of a primitive in the list above, none of them were used.
  warnings.warn(warning_msg, UnusedPrimitiveWarning)


In [9]:
# DFS with default primitives
feature_matrix, feature_names  = ft.dfs(entityset=es, target_dataframe_name='app',
                       trans_primitives=default_trans_primitives,
                       agg_primitives=default_agg_primitives, 
                       max_depth=2, features_only=False, verbose=True)

pd.options.display.max_columns = 1700
feature_matrix.head(10)

Built 2209 features
Elapsed: 00:00 | Progress:  18%|█▊        

/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function amin at 0x1036d3c70> is currently using SeriesGroupBy.min. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "min" instead.
  ).agg(to_agg)
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function mean at 0x1036d8700> is currently using SeriesGroupBy.mean. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "mean" instead.
  ).agg(to_agg)
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function sum at 0x1036d3250> is currently using SeriesGroupBy.sum. In a future version of panda

Elapsed: 00:00 | Progress:  37%|███▋      

/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:839: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pdtypes.is_categorical_dtype(frame.index):
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function mean at 0x1036d8700> is currently using SeriesGroupBy.mean. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "mean" instead.
  ).agg(to_agg)
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function std at 0x1036d88b0> is currently using SeriesGroupBy.std. In a future version of pandas, the provided callable will be used directly. To keep current beh

Elapsed: 00:00 | Progress:  46%|████▌     

/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:839: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pdtypes.is_categorical_dtype(frame.index):
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function std at 0x1036d88b0> is currently using SeriesGroupBy.std. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "std" instead.
  ).agg(to_agg)
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function mean at 0x1036d8700> is currently using SeriesGroupBy.mean. In a future version of pandas, the provided callable will be used directly. To keep current beha

Elapsed: 00:02 | Progress:  95%|█████████▍

/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:839: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pdtypes.is_categorical_dtype(frame.index):


Elapsed: 00:03 | Progress: 100%|██████████


TARGET NAME_CONTRACT_TYPE CODE_GENDER  FLAG_OWN_CAR  \
SK_ID_CURR                                                        
100002           1         Cash loans           M         False   
100003           0         Cash loans           F         False   
100004           0    Revolving loans           M          True   
100006           0         Cash loans           F         False   
100007           0         Cash loans           M         False   
100008           0         Cash loans           M         False   
100009           0         Cash loans           F          True   
100010           0         Cash loans           M          True   
100011           0         Cash loans           F         False   
100012           0    Revolving loans           M         False   

            FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR                                                                
100002                 True             0          202500.0    406597.5   
100003                False             0          270000.0   1293502.5   
100004                 True             0           67500.0    135000.0   
100006                 True             0          135000.0    312682.5   
100007                 True             0          121500.0    513000.0   
100008                 True             0           99000.0    490495.5   
100009                 True             1          171000.0   1560726.0   
100010                 True             0          360000.0   1530000.0   
100011                 True             0          112500.0   1019610.0   
100012                 True             0          135000.0    405000.0   

            AMT_ANNUITY  AMT_GOODS_PRICE  NAME_TYPE_SUITE  \
SK_ID_CURR                                                  
100002          24700.5         351000.0    Unaccompanied   
100003          35698.5        1129500.0           Family   
100004           6750.0         135000.0    Unaccompanied   
100006          29686.5         297000.0    Unaccompanied   
100007          21865.5         513000.0    Unaccompanied   
100008          27517.5         454500.0  Spouse, partner   
100009          41301.0        1395000.0    Unaccompanied   
100010          42075.0        1530000.0    Unaccompanied   
100011          33826.5         913500.0         Children   
100012          20250.0         405000.0    Unaccompanied   

                NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
SK_ID_CURR                                                        
100002                   Working  Secondary / secondary special   
100003             State servant               Higher education   
100004                   Working  Secondary / secondary special   
100006                   Working  Secondary / secondary special   
100007                   Working  Secondary / secondary special   
100008             State servant  Secondary / secondary special   
100009      Commercial associate               Higher education   
100010             State servant               Higher education   
100011                 Pensioner  Secondary / secondary special   
100012                   Working  Secondary / secondary special   

              NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
SK_ID_CURR                                            
100002      Single / not married  House / apartment   
100003                   Married  House / apartment   
100004      Single / not married  House / apartment   
100006            Civil marriage  House / apartment   
100007      Single / not married  House / apartment   
100008                   Married  House / apartment   
100009                   Married  House / apartment   
100010                   Married  House / apartment   
100011                   Married  House / apartment   
100012      Single / not married  House / apartment   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
SK_ID_CURR                            

In [10]:
feature_names[-20:]

[<Feature: STD(credit.previous.SELLERPLACE_AREA)>,
 <Feature: SUM(credit.previous.AMT_ANNUITY)>,
 <Feature: SUM(credit.previous.AMT_APPLICATION)>,
 <Feature: SUM(credit.previous.AMT_CREDIT)>,
 <Feature: SUM(credit.previous.AMT_DOWN_PAYMENT)>,
 <Feature: SUM(credit.previous.AMT_GOODS_PRICE)>,
 <Feature: SUM(credit.previous.CNT_PAYMENT)>,
 <Feature: SUM(credit.previous.DAYS_DECISION)>,
 <Feature: SUM(credit.previous.DAYS_FIRST_DRAWING)>,
 <Feature: SUM(credit.previous.DAYS_FIRST_DUE)>,
 <Feature: SUM(credit.previous.DAYS_LAST_DUE)>,
 <Feature: SUM(credit.previous.DAYS_LAST_DUE_1ST_VERSION)>,
 <Feature: SUM(credit.previous.DAYS_TERMINATION)>,
 <Feature: SUM(credit.previous.HOUR_APPR_PROCESS_START)>,
 <Feature: SUM(credit.previous.NFLAG_INSURED_ON_APPROVAL)>,
 <Feature: SUM(credit.previous.NFLAG_LAST_APPL_IN_DAY)>,
 <Feature: SUM(credit.previous.RATE_DOWN_PAYMENT)>,
 <Feature: SUM(credit.previous.RATE_INTEREST_PRIMARY)>,
 <Feature: SUM(credit.previous.RATE_INTEREST_PRIVILEGED)>,
 <Feature:

In [11]:
feature_matrix_spec, feature_names_spec = ft.dfs(entityset = es, target_dataframe_name = 'app',  
                                                 agg_primitives = ['sum', 'count', 'min', 'max', 'mean', 'mode'], 
                                                 max_depth = 2, features_only = False, verbose = True)

Built 1207 features
Elapsed: 00:00 | Progress:  47%|████▋     

/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function amin at 0x1036d3c70> is currently using SeriesGroupBy.min. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "min" instead.
  ).agg(to_agg)
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function mean at 0x1036d8700> is currently using SeriesGroupBy.mean. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "mean" instead.
  ).agg(to_agg)
/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:829: FutureWarning: The provided callable <function sum at 0x1036d3250> is currently using SeriesGroupBy.sum. In a future version of panda

Elapsed: 00:00 | Progress:  95%|█████████▍

/Users/user/mambaforge/lib/python3.10/site-packages/featuretools/computational_backends/feature_set_calculator.py:839: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pdtypes.is_categorical_dtype(frame.index):


Elapsed: 00:01 | Progress: 100%|██████████


In [12]:
pd.options.display.max_columns = 1000
feature_matrix_spec.head(10)

TARGET NAME_CONTRACT_TYPE CODE_GENDER  FLAG_OWN_CAR  \
SK_ID_CURR                                                        
100002           1         Cash loans           M         False   
100003           0         Cash loans           F         False   
100004           0    Revolving loans           M          True   
100006           0         Cash loans           F         False   
100007           0         Cash loans           M         False   
100008           0         Cash loans           M         False   
100009           0         Cash loans           F          True   
100010           0         Cash loans           M          True   
100011           0         Cash loans           F         False   
100012           0    Revolving loans           M         False   

            FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR                                                                
100002                 True             0          202500.0    406597.5   
100003                False             0          270000.0   1293502.5   
100004                 True             0           67500.0    135000.0   
100006                 True             0          135000.0    312682.5   
100007                 True             0          121500.0    513000.0   
100008                 True             0           99000.0    490495.5   
100009                 True             1          171000.0   1560726.0   
100010                 True             0          360000.0   1530000.0   
100011                 True             0          112500.0   1019610.0   
100012                 True             0          135000.0    405000.0   

            AMT_ANNUITY  AMT_GOODS_PRICE  NAME_TYPE_SUITE  \
SK_ID_CURR                                                  
100002          24700.5         351000.0    Unaccompanied   
100003          35698.5        1129500.0           Family   
100004           6750.0         135000.0    Unaccompanied   
100006          29686.5         297000.0    Unaccompanied   
100007          21865.5         513000.0    Unaccompanied   
100008          27517.5         454500.0  Spouse, partner   
100009          41301.0        1395000.0    Unaccompanied   
100010          42075.0        1530000.0    Unaccompanied   
100011          33826.5         913500.0         Children   
100012          20250.0         405000.0    Unaccompanied   

                NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
SK_ID_CURR                                                        
100002                   Working  Secondary / secondary special   
100003             State servant               Higher education   
100004                   Working  Secondary / secondary special   
100006                   Working  Secondary / secondary special   
100007                   Working  Secondary / secondary special   
100008             State servant  Secondary / secondary special   
100009      Commercial associate               Higher education   
100010             State servant               Higher education   
100011                 Pensioner  Secondary / secondary special   
100012                   Working  Secondary / secondary special   

              NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
SK_ID_CURR                                            
100002      Single / not married  House / apartment   
100003                   Married  House / apartment   
100004      Single / not married  House / apartment   
100006            Civil marriage  House / apartment   
100007      Single / not married  House / apartment   
100008                   Married  House / apartment   
100009                   Married  House / apartment   
100010                   Married  House / apartment   
100011                   Married  House / apartment   
100012      Single / not married  House / apartment   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
SK_ID_CURR                            

In [17]:
from featuretools import selection

# Remove features with only one unique value
feature_matrix2 = selection.remove_low_information_features(feature_matrix_spec)

print('Removed %d features' % (feature_matrix2.shape[1]- feature_matrix_spec.shape[1]))

Removed -121 features


In [16]:
feature_matrix2

TARGET NAME_CONTRACT_TYPE CODE_GENDER  FLAG_OWN_CAR  \
SK_ID_CURR                                                        
100002           1         Cash loans           M         False   
100003           0         Cash loans           F         False   
100004           0    Revolving loans           M          True   
100006           0         Cash loans           F         False   
100007           0         Cash loans           M         False   
...            ...                ...         ...           ...   
106852        <NA>         Cash loans           M         False   
106853        <NA>         Cash loans           M          True   
106854        <NA>         Cash loans           F         False   
106861        <NA>         Cash loans           F         False   
106873        <NA>         Cash loans           M         False   

            FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR                                                                
100002                 True             0          202500.0    406597.5   
100003                False             0          270000.0   1293502.5   
100004                 True             0           67500.0    135000.0   
100006                 True             0          135000.0    312682.5   
100007                 True             0          121500.0    513000.0   
...                     ...           ...               ...         ...   
106852                 True             2          225000.0    177768.0   
106853                False             0          202500.0    479700.0   
106854                 True             0          202500.0    574402.5   
106861                False             0          112500.0    677664.0   
106873                 True             1          157500.0    199152.0   

            AMT_ANNUITY  AMT_GOODS_PRICE NAME_TYPE_SUITE  \
SK_ID_CURR                                                 
100002          24700.5         351000.0   Unaccompanied   
100003          35698.5        1129500.0          Family   
100004           6750.0         135000.0   Unaccompanied   
100006          29686.5         297000.0   Unaccompanied   
100007          21865.5         513000.0   Unaccompanied   
...                 ...              ...             ...   
106852          14175.0         135000.0             NaN   
106853          49153.5         450000.0   Unaccompanied   
106854          29457.0         495859.5   Unaccompanied   
106861          29979.0         585000.0   Unaccompanied   
106873          10800.0         135000.0   Unaccompanied   

                NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
SK_ID_CURR                                                        
100002                   Working  Secondary / secondary special   
100003             State servant               Higher education   
100004                   Working  Secondary / secondary special   
100006                   Working  Secondary / secondary special   
100007                   Working  Secondary / secondary special   
...                          ...                            ...   
106852             State servant               Higher education   
106853      Commercial associate  Secondary / secondary special   
106854                   Working  Secondary / secondary special   
106861                   Working  Secondary / secondary special   
106873                   Working  Secondary / secondary special   

              NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
SK_ID_CURR                                            
100002      Single / not married  House / apartment   
100003                   Married  House / apartment   
100004      Single / not married  House / apartment   
100006            Civil marriage  House / apartment   
100007      Single / not married  House / apartment   
...                          ...                ...   
106852                   Married  House / apartment   
106853      Sing